In [1]:
from app_settings import (
    DOCUMENT_DB_URI,
    AZURE_PRIMARY_KEY, AZURE_URL,
    GEMINI_API_KEY,
    connect_to_cosmosdb
)
from rag.indexing import insert_articles, EmbeddingService
from azure.cosmos import PartitionKey
import pandas as pd
import warnings 
warnings.filterwarnings("ignore")

Project root path: C:\Users\tiago\Documents\NOVA IMS\Data Science\3rd year\Fall\Capstone_Project\Project\deNoise


# Trying out RAG

## Chunking and Indexing

### Inserting the articles in the articles container

In [2]:
news = pd.read_csv("news_database.csv")
news.head()

id                                              title  \
0  19a4eb9435eaa367_2         OpenAI, Amazon Sign $38 Billion Cloud Deal   
1  19a4eb9435eaa367_3  Facebook Dating Is a Surprise Hit for the Soci...   
2  19a4eb9435eaa367_4  A commercial space station startup now has a f...   
3  19a4eb9435eaa367_5  Alphabet is increasingly launching ‘moonshot' ...   
4  19a4eb9435eaa367_7                                               Rmlx   

                                                text                 date  
0  OpenAI will pay Amazon $38 billion for computi...  2025-11-04 11:55:54  
1  Facebook Dating debuted in 2019. The feature l...  2025-11-04 11:55:54  
2  Vast's Haven Demo mission launched into orbit ...  2025-11-04 11:55:54  
3  Alphabet's X Moonshot factory is increasingly ...  2025-11-04 11:55:54  
4  Rmlx is an R interface to Apple's MLX framewor...  2025-11-04 11:55:54

In [3]:
cosmosdb_client, deNoise_cosmosdb = connect_to_cosmosdb()

In [4]:
for cont in deNoise_cosmosdb.list_containers():
    print(cont['id'])

newsArticles
userProfiles


In [5]:
newscontainer = deNoise_cosmosdb.get_container_client('newsArticles')

In [6]:
#insert_articles(deNoise_cosmosdb, 'newsArticles', news)

In [7]:
[article['title'] for article in list(newscontainer.read_all_items())][:5]

['OpenAI, Amazon Sign $38 Billion Cloud Deal',
 'Facebook Dating Is a Surprise Hit for the Social Network',
 'A commercial space station startup now has a foothold in space',
 "Alphabet is increasingly launching ‘moonshot' projects as independent companies — here's why",
 'Rmlx']

In [8]:
len(list(newscontainer.read_all_items()))

669

#### MongoDB database (to delete)

In [9]:
## connect to the document database
#mongodb_client, deNoise_mongodb = connect_to_documentdb()
#
## remove the news articles from the document database
#deNoise_mongodb['news_articles'].delete_many({})
#
#insert_articles(deNoise_mongodb, 
#                'news_articles',
#                news)
#
#len(list(deNoise_mongodb['news_articles'].find()))

### Embeddings

In [9]:
text = list(newscontainer.read_all_items())[0]['title']
print(text)
type(text)

OpenAI, Amazon Sign $38 Billion Cloud Deal


str

In [10]:
embeddingservice = EmbeddingService()
result = embeddingservice.generate_embedding(text=text)
result

[-0.0070019662,
 -0.0023241008,
 0.0044640778,
 -0.084099464,
 -0.011027054,
 0.004685113,
 0.039817106,
 0.019069528,
 -0.008995239,
 2.6935886e-05,
 -0.03661413,
 -0.0026772444,
 0.015470704,
 -0.007611877,
 0.109608755,
 0.011998819,
 0.014253483,
 -0.011594762,
 0.0155390175,
 0.0043275524,
 -0.010480972,
 -0.010693609,
 0.03183914,
 0.000721525,
 -0.0025996692,
 -0.008987109,
 0.026555033,
 -0.015239678,
 0.021596592,
 -0.008127287,
 -0.0048588375,
 -0.018267676,
 0.021259096,
 0.032728598,
 -0.010860972,
 0.028622821,
 0.02268366,
 -0.011431093,
 -0.0053429347,
 0.016993133,
 -0.0060531744,
 0.00951269,
 0.011424423,
 0.0051925275,
 -0.026201677,
 -0.022788472,
 0.0051345276,
 -0.019273147,
 -0.041176785,
 -0.0015840643,
 0.0032653955,
 0.001473156,
 -0.00054675917,
 -0.17107475,
 -0.005040998,
 0.012111169,
 0.0085012,
 0.0010916906,
 -0.008958267,
 0.0060346485,
 0.0052046534,
 0.020759093,
 -0.022948097,
 -0.0016393813,
 -0.026198698,
 -0.01891186,
 -0.0057785283,
 0.005322587

In [11]:
results = embeddingservice.embed_documents(texts=[article['text'] for article in list(newscontainer.read_all_items())[:10]])
results

✅ Processed 10/10 embeddings
✅ Completed: 10/10 embeddings generated


[[0.0027072832,
  0.0011487498,
  0.0072176815,
  -0.06966001,
  -0.0055333897,
  0.0071876855,
  0.030943887,
  0.016082335,
  0.010407427,
  0.003083017,
  -0.017617293,
  0.020991115,
  0.025451707,
  -0.009460841,
  0.118922286,
  0.022543425,
  0.025001694,
  0.006421748,
  0.03213093,
  0.015801037,
  -0.0054936553,
  -0.00995614,
  0.022128595,
  0.0049265954,
  -0.0091924155,
  -0.0072244145,
  0.022609562,
  -0.005887547,
  0.020862626,
  -0.020182047,
  -0.014727929,
  -0.01626627,
  0.019369919,
  0.044537205,
  0.013661189,
  0.02308077,
  0.022346001,
  -0.012267383,
  0.01003225,
  0.016817223,
  0.001097821,
  -0.0024539891,
  0.009035611,
  -0.016897615,
  -0.021792023,
  -0.02659285,
  0.011525224,
  -0.024910372,
  -0.0196952,
  0.0032165472,
  -0.013740063,
  0.00075184146,
  0.0106532965,
  -0.16678189,
  -0.0008317927,
  0.004823209,
  0.011111902,
  -0.005270322,
  0.008293994,
  0.014416186,
  -0.006728737,
  0.03366766,
  -0.02095875,
  -0.02302042,
  -0.0210880

In [45]:
embeddingscontainer = deNoise_cosmosdb.get_container_client('newsEmbeddings')

In [47]:

from app_settings import COSMOSDB_INDEXING_POLICY, COSMOSDB_VECTOR_EMBEDDING_POLICY, COSMOSDB_VECTOR_SEARCH_FIELDS

deNoise_cosmosdb.create_container_if_not_exists( 
    id='vectorStore', 
    partition_key=PartitionKey(path='/id'), 
    indexing_policy=COSMOSDB_INDEXING_POLICY, 
    vector_embedding_policy=COSMOSDB_VECTOR_EMBEDDING_POLICY) 


print('Container with id \'vectorStore\' created') 

Container with id 'vectorStore' created


In [3]:
list(newscontainer.read_all_items())[0]['date']

NameError: name 'newscontainer' is not defined

# Deleting the articles from the newsEmbeddings container

In [2]:
def recreate_embeddings_container():
    """
    Delete and recreate the newsEmbeddings container.
    This is the fastest way to clear all data.
    """
    from app_settings import COSMOSDB_INDEXING_POLICY, COSMOSDB_VECTOR_EMBEDDING_POLICY
    
    cosmosdb_client, cosmos_db = connect_to_cosmosdb()
    
    # Delete the container
    try:
        cosmos_db.delete_container('newsEmbeddings')
        print("🗑️  Deleted newsEmbeddings container")
    except Exception as e:
        print(f"⚠️  Container might not exist: {e}")
    
    # Recreate the container
    partition_key = PartitionKey(path="/id")
    
    cosmos_db.create_container_if_not_exists(
        id='newsEmbeddings',
        partition_key=partition_key,
        indexing_policy=COSMOSDB_INDEXING_POLICY,
        vector_embedding_policy=COSMOSDB_VECTOR_EMBEDDING_POLICY
    )
    
    print("✅ Recreated newsEmbeddings container")


recreate_embeddings_container()

🗑️  Deleted newsEmbeddings container
✅ Recreated newsEmbeddings container


# Index the articles

In [4]:
cosmosdb_client, deNoise_cosmosdb = connect_to_cosmosdb()
newscontainer = deNoise_cosmosdb.get_container_client('newsArticles')

In [5]:
len(list(deNoise_cosmosdb.get_container_client('newsEmbeddings').read_all_items()))

0

In [6]:
len(list(newscontainer.read_all_items()))

669

In [7]:
from rag.indexing import index_article
not_indexed_ids = []
all_articles = list(newscontainer.read_all_items())
current_indexed_count = 0

for article in all_articles:
    print(article['title'])
    try:
        index_article(
            contents=[article['title'], article['text']],
            article_title=article['title'],
            article_id=article['id'],
            article_date=article['date']
        )
        print("✅ Indexed successfully")
    
    except Exception as e:
        error_msg = str(e)
        print(f"❌ Error: {error_msg}")
        
        # Check if it's a quota/API limit error
        if any(keyword in error_msg.lower() for keyword in ['quota', 'rate limit', '429', 'resource exhausted', 'limit exceeded']):
            print(f"\n⚠️ API quota exhausted. Stopping indexing.")
            not_indexed_ids.append(article['id'])
            
            # Get all remaining article IDs
            current_index = all_articles.index(article)
            remaining_articles = all_articles[current_index + 1:]
            not_indexed_ids.extend([art['id'] for art in remaining_articles])
            
            break
        else:
            # Other error - add to list and continue
            not_indexed_ids.append(article['id'])
            continue

# Save not indexed IDs to file
with open('not_indexed_articles.txt', 'w') as f:
    for article_id in not_indexed_ids:
        f.write(f"{article_id}\n")

print(f"\n📊 Summary:")
print(f"⏭️  Not indexed: {len(not_indexed_ids)} articles")
print(f"💾 IDs saved to 'not_indexed_articles.txt'")

OpenAI, Amazon Sign $38 Billion Cloud Deal
✅ Completed: 2/2 embeddings generated
✅ Indexed successfully
Facebook Dating Is a Surprise Hit for the Social Network
❌ Error generating embedding: 429 RESOURCE_EXHAUSTED. {'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits. To monitor your current usage, head to: https://ai.dev/usage?tab=rate-limit. \n* Quota exceeded for metric: generativelanguage.googleapis.com/embed_content_free_tier_requests, limit: 0', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/embed_content_free_tier_requests', 'quotaId': 

KeyboardInterrupt: 

In [ ]:
from rag.indexing import index_article

# Read the not indexed article IDs from file
with open('not_indexed_articles.txt', 'r') as f:
    not_indexed_ids = [line.strip() for line in f.readlines()]

print(f"📋 Found {len(not_indexed_ids)} articles to index")

# Get the newscontainer
cosmosdb_client, deNoise_cosmosdb = connect_to_cosmosdb()
newscontainer = deNoise_cosmosdb.get_container_client('newsArticles')

# Track progress
still_not_indexed = []
successfully_indexed = []

for i, article_id in enumerate(not_indexed_ids):
    # Find the article in the container
    article = None
    for item in newscontainer.read_all_items():
        if item['id'] == article_id:
            article = item
            break
    
    if not article:
        print(f"⚠️ Article ID {article_id} not found in container")
        still_not_indexed.append(article_id)
        continue
    
    print(f"[{i+1}/{len(not_indexed_ids)}] {article['title']}")
    
    try:
        index_article(
            contents=[article['title'], article['text']],
            article_title=article['title'],
            article_id=article['id'],
            article_date=article['date']
        )
        successfully_indexed.append(article_id)
        print("✅ Indexed successfully")
        
    except Exception as e:
        error_msg = str(e)
        print(f"❌ Error: {error_msg}")
        
        # Check if it's a quota/API limit error
        if any(keyword in error_msg.lower() for keyword in ['quota', 'rate limit', '429', 'resource exhausted', 'limit exceeded']):
            print(f"\n⚠️ API quota exhausted again. Stopping.")
            
            # Save remaining IDs
            still_not_indexed.extend(not_indexed_ids[i:])
            break
        else:
            # Other error - add to list and continue
            still_not_indexed.append(article_id)
            continue

# Update the file with remaining articles
with open('not_indexed_articles.txt', 'w') as f:
    for article_id in still_not_indexed:
        f.write(f"{article_id}\n")

print(f"\n📊 Final Summary:")
print(f"✅ Successfully indexed: {len(successfully_indexed)} articles")
print(f"⏭️  Still not indexed: {len(still_not_indexed)} articles")
print(f"💾 Updated 'not_indexed_articles.txt'")

In [ ]:
#from rag.indexing import index_article
#for article in list(newscontainer.read_all_items()):
#    print(article['title'])
#    index_article(
#        contents = [article['title'], article['text']],
#        article_title = article['title'],
#        article_id = article['id'],
#        article_date = article['date']
#    )

Facebook Dating Is a Surprise Hit for the Social Network
✅ Completed: 2/2 embeddings generated
A commercial space station startup now has a foothold in space
✅ Completed: 2/2 embeddings generated
Alphabet is increasingly launching ‘moonshot' projects as independent companies — here's why
✅ Completed: 2/2 embeddings generated
Rmlx
✅ Completed: 2/2 embeddings generated
The fetch()ening
✅ Completed: 2/2 embeddings generated
The Great Decoupling of Labor and Capital
✅ Completed: 2/2 embeddings generated
The Startup Winter Is Always Coming
✅ Completed: 2/2 embeddings generated
An individual can change an organization
✅ Completed: 2/2 embeddings generated
rm -rf remains
✅ Completed: 2/2 embeddings generated
Introducing Generalized Consensus: An Alternate Approach to Distributed Durability
✅ Completed: 2/2 embeddings generated
Chrome can now autofill driver's license, vehicle info, and more
✅ Completed: 2/2 embeddings generated
Is it worrying that 95% of AI enterprise projects fail?
✅ Complet

ServiceRequestError: HTTPSConnection(host='denoise.documents.azure.com', port=443): Failed to resolve 'denoise.documents.azure.com' ([Errno 11001] getaddrinfo failed)

In [39]:
embeddings_container = deNoise_cosmosdb.get_container_client('newsEmbeddings')
repeated_articles = []
for article in list(newscontainer.read_all_items()):
    #print(article['title'])
    # Check if article already exists
    query = "SELECT VALUE COUNT(1) FROM c WHERE c.metadata.article_id = @article_id"
    parameters = [{"name": "@article_id", "value": str(article['id'])}]
    
    count = list(embeddings_container.query_items(
        query=query,
        parameters=parameters,
        enable_cross_partition_query=True
    ))[0]
    print(count)
    if count != 2:
        print(article['title'])
        print(article['id'])
        print('###############################################')
        repeated_articles.append(article['id'])
        #print(f"⏭️  Skipping '{article['title']}' (already indexed)")
        continue


    #index_article(
    #    contents = [article['title'], article['text']],
    #    article_title = article['title'],
    #    article_id = article['id'],
    #    article_date = article['date']
    #)

2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
4
Why Signal's post-quantum makeover is an amazi

In [40]:
repeated_articles

['199e25db972bf322_10',
 '199e25db972bf322_11',
 '199e25db972bf322_12',
 '199e25db972bf322_13',
 '199e25db972bf322_15',
 '199e25db972bf322_16',
 '199e25db972bf322_17',
 '199e21d51bd5e158_1',
 '199e21d51bd5e158_2',
 '199e21d51bd5e158_3',
 '199e21d51bd5e158_4',
 '199e21d51bd5e158_5',
 '199e21d51bd5e158_6',
 '199e21d51bd5e158_7',
 '199e21d51bd5e158_8',
 '199e21d51bd5e158_9',
 '199e21d51bd5e158_10',
 '199e21d51bd5e158_11',
 '199e21d51bd5e158_12',
 '199e21d51bd5e158_13',
 '199e21d51bd5e158_14',
 '199dd367dda8ed83_2',
 '199dd367dda8ed83_3',
 '199dd367dda8ed83_4',
 '199dd367dda8ed83_5',
 '199dd367dda8ed83_6',
 '199dd367dda8ed83_7',
 '199dd367dda8ed83_8',
 '199dd367dda8ed83_9',
 '199dd367dda8ed83_10',
 '199dd367dda8ed83_11',
 '199dd367dda8ed83_12',
 '199dd367dda8ed83_14',
 '199dd367dda8ed83_15',
 '199dd367dda8ed83_16',
 '199d2b94feaa535e_1',
 '199d2b94feaa535e_2',
 '199d2b94feaa535e_3',
 '199d2b94feaa535e_4',
 '199d2b94feaa535e_5',
 '199d2b94feaa535e_6',
 '199d2b94feaa535e_7',
 '199d2b94feaa53

In [5]:
from langchain_azure_ai.vectorstores import AzureCosmosDBNoSqlVectorSearch
from rag.indexing import EmbeddingService
from azure.cosmos import PartitionKey
from app_settings import (COSMOSDB_INDEXING_POLICY, COSMOSDB_VECTOR_SEARCH_FIELDS, COSMOSDB_VECTOR_EMBEDDING_POLICY)

title_to_find = "Dutch government takes control of Chinese-owned chipmaker Nexperia in ‘highly exceptional' move"

embeddings = EmbeddingService()

def search_by_title_vector(article_title: str, query_text: str = None, k: int = 5) -> list:
    """
    Search vector database with title filter and optional semantic query.
    
    Args:
        article_title: Filter results to this article title
        query_text: Optional text to semantically search within the article
        k: Number of results to return
        
    Returns:
        List of matching documents with similarity scores
    """
    cosmosdb_client, cosmos_db = connect_to_cosmosdb()

    partition_key = PartitionKey(path="/id")
    cosmos_container_properties = {"partition_key": partition_key}

    # Initialize vector search
    vector_search = AzureCosmosDBNoSqlVectorSearch(
        cosmos_client=cosmosdb_client,
        embedding=embeddings,
        database_name='deNoise',
        container_name='vectorStore',
        vector_embedding_policy=COSMOSDB_VECTOR_EMBEDDING_POLICY,
        indexing_policy=COSMOSDB_INDEXING_POLICY,
        vector_search_fields=COSMOSDB_VECTOR_SEARCH_FIELDS,
        cosmos_database_properties={},
        cosmos_container_properties=cosmos_container_properties
    )
    
    # Search with metadata filter
    if query_text:
        # Semantic search within the article
        results = vector_search.similarity_search(
            query=query_text,
            k=k,
            filters={"title": article_title}
        )
    else:
        # Just retrieve chunks by title (using title as query)
        results = vector_search.similarity_search(
            query=article_title,
            k=k,
            filters={"title": article_title}
        )
    
    return results

search_by_title_vector('OpenAI and Amazon')

[Document(metadata={'title': 'OpenAI, Amazon Sign $38 Billion Cloud Deal', 'article_id': '19a4eb9435eaa367_2', 'date': '2025-11-04 11:55:54', 'is_title': True, 'id': '75724366-8ffd-4b09-b282-44d854d655c6'}, page_content='"OpenAI, Amazon Sign $38 Billion Cloud Deal"'),
 Document(metadata={'title': 'OpenAI, Amazon Sign $38 Billion Cloud Deal', 'article_id': '19a4eb9435eaa367_2', 'date': '2025-11-04 11:55:54', 'is_title': False, 'id': '875850ab-bd4b-4fc3-8b49-ffb1018386af'}, page_content='"OpenAI will pay Amazon $38 billion for computing power in a multiyear deal. Amazon expects all of the computing capacity negotiated as part of the agreement to be available by the end of the year. It wasn\'t able to sell its cloud services to OpenAI for years because OpenAI had an exclusive cloud-computing partnership with Microsoft. OpenAI is set to generate $13 billion in revenue this year. It will have to continue expanding sales at an exponential rate to pay for its computing needs. Sam Altman claim

In [41]:
#article_id = '199e25db972bf322_9'
cosmosdb_client, cosmos_db = connect_to_cosmosdb()
embeddings_container = cosmos_db.get_container_client('newsEmbeddings')

for id in repeated_articles:
    print('\n\n')
    print(id)
    # Find all chunks for this article
    query = "SELECT * FROM c WHERE c.metadata.article_id = @article_id"
    parameters = [{"name": "@article_id", "value": id}]

    chunks = list(embeddings_container.query_items(
        query=query,
        parameters=parameters,
        enable_cross_partition_query=True
    ))
    print(chunks)
    ## Delete each chunk
    #deleted_count = 0
    #for chunk in chunks:
    #    embeddings_container.delete_item(
    #        item=chunk['id'],
    #        partition_key=chunk['id']
    #    )
    #    deleted_count += 1
    #
    #print(f"🗑️  Deleted {deleted_count} chunks for article: {title}")




199e25db972bf322_10
[{'id': 'fc598558-10ae-42b1-8d8b-4ecc86480d7d', 'content': '"Why Signal\'s post-quantum makeover is an amazing engineering achievement"', 'embedding': None, 'metadata': {'title': "Why Signal's post-quantum makeover is an amazing engineering achievement", 'article_id': '199e25db972bf322_10', 'date': '2025-10-14 11:56:56', 'is_title': True}, '_rid': '3RwKAJpiSte5AwAAAAAAAA==', '_self': 'dbs/3RwKAA==/colls/3RwKAJpiStc=/docs/3RwKAJpiSte5AwAAAAAAAA==/', '_etag': '"00000809-0000-5300-0000-69346bb10000"', '_attachments': 'attachments/', '_ts': 1765043121}, {'id': 'b54afb35-2fe2-4854-a941-80c4110745e9', 'content': '"Signal\'s latest updates are a significant step towards the messaging platform becoming fully quantum-resistant. Nothing will change for users as the changes are all under-the-hood - the apps will behave almost exactly as they did before. Signal has documented in great depth about the new design along with mathematical proof verifying that the updated protoco

In [38]:
cosmosdb_client, deNoise_cosmosdb = connect_to_cosmosdb()
newscontainer = deNoise_cosmosdb.get_container_client('newsArticles')
results = []
for title in repeated_articles:
    query = "SELECT * FROM c WHERE c.title = @title"
    parameters = [{"name": "@title", "value": title}]

    result = list(newscontainer.query_items(
        query=query,
        parameters=parameters,
        enable_cross_partition_query=True
    ))
    results.extend(result)
    #print(result)
    #print(len(result))
    if len(result) > 1:
        for res in result:
            print(res)


{'id': '19a4949c75ce5b52_7', 'title': 'The week ahead', 'text': 'President Trump’s tariffs are before the Supreme Court: — Justices will hear arguments on Wednesday over whether the bulk of the president’s sweeping tariffs pass legal muster. The US Constitution says it’s up to Congress to set taxes and duties, but the White House argues that trade deficits with other countries are a national emergency, and that clears the way for the president to have broad tariff powers. If the court ends up ruling against the administration, it won’t wipe away all of Trump’s tariffs, but it could water down one of his most powerful trade weapons. Tesla shareholders will vote on Elon Musk’s massive new compensation package: — Shareholders will have a lot of zeroes to consider at Tesla’s annual meeting this Thursday. If approved, Musk’s new pay plan could be worth a trillion dollars if he hits certain ambitious milestones for the company. Board Chair Robyn Denholm has urged shareholders to green-light 

In [35]:
display(len(results) )
len(repeated_articles)

93

86

In [11]:
index_article(
    contents = [list(newscontainer.read_all_items())[475]['title'], list(newscontainer.read_all_items())[475]['text']],
    article_title = list(newscontainer.read_all_items())[475]['title'],
    article_id = list(newscontainer.read_all_items())[475]['id'],
    article_date = list(newscontainer.read_all_items())[475]['date']
)

NameError: name 'index_article' is not defined

### Testing similarity Search

In [ ]:
from langchain_azure_ai.vectorstores import AzureCosmosDBNoSqlVectorSearch


vector_search = AzureCosmosDBNoSqlVectorSearch.from_documents(
        documents=documents,
        embedding=embeddings,
        cosmos_client=cosmosdb_client,
        database_name='deNoise',
        container_name=container_name,
        full_text_policy=None,
        indexing_policy=COSMOSDB_INDEXING_POLICY,
        vector_embedding_policy=COSMOSDB_VECTOR_EMBEDDING_POLICY,
        cosmos_container_properties=cosmos_container_properties,
        vector_search_fields=COSMOSDB_VECTOR_SEARCH_FIELDS,
        cosmos_database_properties={},
        full_text_search_enabled=False
    )